In [281]:
import pandas as pd
import json
import numpy
import geopy.distance
import math
import sys


In [313]:
dataset = pd.read_csv("partial_subtracks_with_extra_points_after_dividing_only_city_centre.csv")

In [284]:
# calculate the distance between the two points


def point_distance(point1, point2):
    p1 = (point1[0], point1[1])
    p2 = (point2[0], point2[1])
    dist = geopy.distance.distance(p1, p2).m
    if dist > 30:
        return -1
    else:
        return 1

In [285]:
def actual_distance(point1, point2):
    p1 = (point1[0], point1[1])
    p2 = (point2[0], point2[1])
    dist = geopy.distance.distance(p1, p2).m
    return dist

In [301]:
gap_penalty = -1

def create_matrix(track1, track2):
    matrix = numpy.zeros((len(track1) + 1, len(track2) + 1))
    for i in range(0, len(track1) + 1):
        matrix[i, 0] = gap_penalty * i
    for j in range(0, len(track2) + 1):
        matrix[0, j] = gap_penalty * j

    for i in range(1, len(track1) + 1):
        t1 = track1[i - 1]
        for j in range(1, len(track2) + 1):
            t2 = track2[j - 1]
            match = matrix[i - 1, j - 1] + point_distance(t1, t2)
            delete = matrix[i - 1, j] + gap_penalty
            insert = matrix[i, j - 1] + gap_penalty
            matrix[i, j] = max(match, max(delete, insert))

    return matrix


#track1 = dataset.loc[dataset["id"] == "T1"].values.tolist()
#track2 = dataset.loc[dataset["id"] == "T2"].values.tolist()
#matrix = create_matrix(track1, track2)
#print(matrix)

[[  0.  -1.  -2.  -3.  -4.  -5.  -6.  -7.  -8.  -9. -10. -11. -12. -13.
  -14. -15. -16. -17. -18. -19. -20. -21. -22. -23. -24. -25. -26. -27.
  -28. -29. -30. -31. -32. -33. -34. -35. -36. -37. -38. -39. -40. -41.
  -42. -43. -44. -45. -46. -47. -48. -49. -50. -51. -52. -53. -54. -55.
  -56. -57. -58. -59. -60. -61. -62. -63. -64. -65. -66. -67. -68. -69.
  -70. -71. -72. -73. -74. -75. -76. -77.]
 [ -1.  -1.  -2.  -3.  -4.  -5.  -6.  -7.  -8.  -9. -10. -11. -12. -13.
  -14. -15. -16. -17. -18. -19. -20. -21. -22. -23. -24. -25. -26. -27.
  -28. -29. -30. -31. -32. -33. -34. -35. -36. -37. -38. -39. -40. -41.
  -42. -43. -44. -45. -46. -47. -48. -49. -50. -51. -52. -53. -54. -55.
  -56. -57. -58. -59. -60. -61. -62. -63. -64. -65. -66. -67. -68. -69.
  -70. -71. -72. -73. -74. -75. -76. -77.]
 [ -2.  -2.  -2.  -3.  -4.  -5.  -6.  -7.  -8.  -9. -10. -11. -12. -13.
  -14. -15. -16. -17. -18. -19. -20. -21. -22. -23. -24. -25. -26. -27.
  -28. -29. -30. -31. -32. -33. -34. -35. -36. -37

In [306]:
def backtrack(matrix, track1, track2):

    i = len(track1)
    j = len(track2)

    a1 = []

    while i > 0 and j > 0:
        if (
            matrix[i, j] == matrix[i - 1, j - 1] + 1
            and point_distance(
                (track1[i - 1][0], track1[i - 1][1]),
                (track2[j - 1][0], track2[j - 1][1]),
            )
            > 0
        ):
            a1.insert(0, [track1[i - 1][0], track1[i - 1][1], track2[0][2]])
            i = i - 1
            j = j - 1
        elif matrix[i, j] == matrix[i - 1, j - 1] - 1:
            i = i - 1
            j = j - 1
        elif matrix[i, j] == matrix[i - 1, j] - 1:
            i = i - 1
        elif matrix[i, j] == matrix[i, j - 1] - 1:
            j = j - 1
        else:
            print("5")
            a1 = []
            break
    return a1


#align = backtrack(matrix, track1, track2)
#print(align)

[]


In [117]:
def check_length(matrix):
    longest_alignment = numpy.max(matrix)
    if longest_alignment <= 3:
        return False
    else:
        return True

In [312]:
track_ids = pd.read_csv("partial_subtracks_ids_add_points_after_dividing.csv").values.tolist()
#track_ids = pd.read_csv("partial_subtracks_ids.csv").values.tolist()

In [318]:

def Needleman_Wunsch(dataset, trackid, nr):
    fulltrack = dataset.loc[dataset["id"] == trackid]
    track = pd.DataFrame.drop_duplicates(fulltrack)
    print("track1: ", trackid)
    alignments = []
    for j in range(nr + 1, len(track_ids)):
        #print("track2: ", track_ids[j][0])
        next_track = dataset.loc[dataset["id"] == track_ids[j][0]]
        matrix = create_matrix(track.values.tolist(), next_track.values.tolist())
        alignment = backtrack(matrix, track.values.tolist(), next_track.values.tolist())
        if (len(alignment) > 3):
            alignments.extend(alignment)
    return alignments


#align = Needleman_Wunsch(dataset, "T1", 0)

In [121]:
def create_list_of_points(tracknr, alignments):
    
    track = dataset.loc[dataset["id"] == tracknr]
    track = pd.DataFrame.drop_duplicates(track)
    points = pd.DataFrame(columns=["lat", "lon", "ids"])
    align = pd.DataFrame(alignments, columns=["lat", "lon", "id"])

    for i in range(len(track)):
        lat = align.loc[align["lat"] == track.iloc[i]["lat"]]
        points.loc[i] = [
            track.iloc[i]["lat"],
            track.iloc[i]["lon"],
            lat["id"].values.tolist(),
        ]
    return points

#points = create_list_of_points("T1", align)
#print(points)

In [122]:
def remove_infrequent_points(points):
    point_list = pd.DataFrame(points, columns=["lat", "lon", "ids"])
    for i in range(len(point_list)):
        val = len(point_list.loc[i]["ids"])
        point_list.at[i, "ids"] = val
    return point_list
#new_points = remove_infrequent_points(points)
#print(new_points)

In [104]:
def gather_sequences(points):
    i = 0
    final_records = pd.DataFrame(columns=["polyline", "value"])
    for group in range(points.iloc[0]["group"], -1, -1):
        records = pd.DataFrame(columns=["polyline", "value"])
        sequence = []
        value = 0
        while i < len(points) and points.iloc[i]["group"] == group:
            if value == points.iloc[i]["ids"] or value == 0:
                sequence.append(
                    [
                        points.index[i],
                        points.iloc[i]["lat"],
                        points.iloc[i]["lon"],
                    ]
                )
                value = points.iloc[i]["ids"]
                i += 1
            else:
                sequence.sort()
                new_sequence = sequence.copy()
                records.loc[len(records)] = [
                    new_sequence,
                    (len(new_sequence) * 1.0) + value,
                ]
                value = points.iloc[i]["ids"]

        sequence.sort()
        new_sequence = sequence.copy()
        records.loc[len(records)] = [
            new_sequence,
            (len(new_sequence) * 1.0) + value,
        ]
        if len(records) < 2:
            final_records = pd.concat([final_records, records])
        else:
            highest_value = records["value"].idxmax()
            final_records = final_records.append(records.loc[highest_value])

    return final_records

new_points['group'] = (new_points.index.to_series().diff() > 1).cumsum()
print(new_points)
new_points.sort_values(by=['group','ids'], ascending=False, inplace=True)
list = gather_sequences(new_points)
print(list)

          lat       lon ids  group
0   41.148522 -8.585676  16      0
1   41.148639 -8.585712  15      0
2   41.148855 -8.585685  17      0
3   41.148927 -8.585730  17      0
4   41.148963 -8.585982  17      0
5   41.148958 -8.586189  16      0
6   41.148954 -8.586396  16      0
7   41.148837 -8.586234  16      0
8   41.148720 -8.586072  13      0
9   41.148720 -8.586072  13      0
10  41.148545 -8.586122   6      0
11  41.148371 -8.586173   6      0
12  41.148196 -8.586223   6      0
13  41.148022 -8.586274   5      0
14  41.147847 -8.586324   5      0
15  41.147847 -8.586324   5      0
16  41.147750 -8.586493   5      0
17  41.147653 -8.586662   5      0
18  41.147557 -8.586830   5      0
19  41.147460 -8.586999   6      0
20  41.147460 -8.586999   5      0
21  41.147307 -8.586787   6      0
22  41.147154 -8.586576   7      0
23  41.147154 -8.586576   7      0
24  41.147095 -8.586388   7      0
25  41.147036 -8.586200   7      0
26  41.146977 -8.586012   7      0
27  41.146918 -8.585

In [107]:
numpy.set_printoptions(threshold=sys.maxsize)
print(list["polyline"].iloc[0])

[[0, 41.148522, -8.585676], [1, 41.148639, -8.585712000000001], [2, 41.148855000000005, -8.585685000000002], [3, 41.14892699999999, -8.585730000000002], [4, 41.148963, -8.585982], [5, 41.1489585, -8.586189000000001], [6, 41.148954, -8.586396], [7, 41.148837, -8.586234000000001], [8, 41.14872, -8.586072000000001], [9, 41.14872, -8.586072], [10, 41.1485454, -8.5861224], [11, 41.1483708, -8.586172800000002], [12, 41.1481962, -8.586223200000003], [13, 41.14802159999999, -8.586273600000004], [14, 41.14784699999999, -8.586324000000005], [15, 41.147847, -8.586324000000001], [16, 41.14775025, -8.586492750000001], [17, 41.1476535, -8.586661500000002], [18, 41.14755675000001, -8.586830250000002], [19, 41.14746000000001, -8.586999000000002], [20, 41.14746, -8.586999], [21, 41.147307, -8.5867875], [22, 41.147154, -8.586575999999999], [23, 41.14715400000001, -8.586575999999999], [24, 41.14709500000001, -8.586388], [25, 41.14703600000001, -8.5862], [26, 41.14697700000001, -8.586012], [27, 41.1469180

In [316]:
def hele_sullamitten(dataset):
    most_tracked_roads = pd.DataFrame(columns = ['polyline', 'value'])
    for i in range(len(track_ids)):
        track = track_ids[i][0]
        alignment = Needleman_Wunsch(dataset, track, i)
        points = create_list_of_points(track, alignment)
        new_points = remove_infrequent_points(points)
        new_points = new_points[new_points.ids > 8]
        if not new_points.empty:
            new_points['group'] = (new_points.index.to_series().diff() > 1).cumsum()
            new_points.sort_values(by=['group','ids'], ascending=False, inplace=True)
            records = gather_sequences(new_points)
            most_tracked_roads = pd.concat([most_tracked_roads, records])
            print(most_tracked_roads)
    return most_tracked_roads

res = hele_sullamitten(dataset)

T1
track1:  T1
track2:  T2
track2:  T2334
track2:  T3
track2:  T3463
track2:  T3569
track2:  T3985
track2:  T4
track2:  T61199
track2:  T612104
track2:  T7
track2:  T74236
track2:  T75244
track2:  T9
track2:  T914261
track2:  T10
track2:  T104294
track2:  T10100298
track2:  T1015330
track2:  T11
track2:  T12
track2:  T1219419
track2:  T137427
track2:  T15
track2:  T1625507
track2:  T1684519
track2:  T1626525
track2:  T17
track2:  T1728548
track2:  T1729551
track2:  T18
track2:  T19
track2:  T1919633
track2:  T1931644
track2:  T20
track2:  T21
track2:  T2238798
track2:  T23
track2:  T24
track2:  T25
track2:  T2641839
track2:  T27
track2:  T28
track2:  T29
track2:  T2923862
track2:  T30
track2:  T304913
track2:  T305922
track2:  T31
track2:  T314952
track2:  T31100959
track2:  T32
track2:  T33
track2:  T33471029
track2:  T33481033
track2:  T33491045
track2:  T3571064
track2:  T35581085
track2:  T36521124
track2:  T36541142
track2:  T36551189
track2:  T36571195
track2:  T37
track2:  T3726

track2:  T256697335
track2:  T257
track2:  T258
track2:  T259
track2:  T260677397
track2:  T260487407
track2:  T260497412
track2:  T260287420
track2:  T261
track2:  T262
track2:  T263677479
track2:  T264
track2:  T265
track2:  T265207512
track2:  T266
track2:  T267
track2:  T2671037532
track2:  T268
track2:  T269
track2:  T269107565
track2:  T270957576
track2:  T270597581
track2:  T270517592
track2:  T270357597
track2:  T271
track2:  T273
track2:  T274
track2:  T275
track2:  T27617694
track2:  T276267719
track2:  T278
track2:  T280627756
track2:  T280267759
track2:  T280677780
track2:  T280577807
track2:  T281
track2:  T28117819
track2:  T28117823
track2:  T282
track2:  T28217836
track2:  T283
track2:  T28317852
track2:  T284
track2:  T286
track2:  T288
track2:  T290
track2:  T290677909
track2:  T291
track2:  T292
track2:  T292677943
track2:  T29217948
track2:  T292417958
track2:  T293287979
track2:  T293237987
track2:  T29318000
track2:  T294
track2:  T294678040
track2:  T295
track2: 

track2:  T211155584
track2:  T21375604
track2:  T214
track2:  T215
track2:  T2171135676
track2:  T217235685
track2:  T217855729
track2:  T217265741
track2:  T218
track2:  T218825795
track2:  T218235806
track2:  T21815857
track2:  T219
track2:  T220155883
track2:  T220535892
track2:  T2201145907
track2:  T220535938
track2:  T221
track2:  T222
track2:  T22215997
track2:  T222146021
track2:  T223376051
track2:  T223366133
track2:  T224
track2:  T224966165
track2:  T224506174
track2:  T224266177
track2:  T2241096194
track2:  T224366198
track2:  T2241166210
track2:  T2241166218
track2:  T224256290
track2:  T224266300
track2:  T224176322
track2:  T224156325
track2:  T225976345
track2:  T225466351
track2:  T225476367
track2:  T225486371
track2:  T225996403
track2:  T225236406
track2:  T225406416
track2:  T226
track2:  T226796448
track2:  T227
track2:  T227196462
track2:  T22716476
track2:  T22846504
track2:  T22846510
track2:  T2281006514
track2:  T22876518
track2:  T228156528
track2:  T22815

track2:  T151
track2:  T151463833
track2:  T151473836
track2:  T151783841
track2:  T152203846
track2:  T153773864
track2:  T154
track2:  T1541103889
track2:  T156
track2:  T156263917
track2:  T158
track2:  T159
track2:  T159233975
track2:  T161663997
track2:  T161674001
track2:  T162284049
track2:  T163
track2:  T163234078
track2:  T166
track2:  T167
track2:  T167194141
track2:  T167314144
track2:  T168644170
track2:  T168524176
track2:  T169754184
track2:  T170
track2:  T170204216
track2:  T171
track2:  T171874234
track2:  T171354258
track2:  T172
track2:  T1721064277
track2:  T173
track2:  T173474306
track2:  T173284331
track2:  T174
track2:  T17404354
track2:  T17444360
track2:  T17454366
track2:  T174154372
track2:  T177
track2:  T179524398
track2:  T179814407
track2:  T179174411
track2:  T17984415
track2:  T17904427
track2:  T18014434
track2:  T181
track2:  T181654460
track2:  T181664465
track2:  T181674471
track2:  T1811024490
track2:  T1811084525
track2:  T181414554
track2:  T18

track2:  T88
track2:  T88192455
track2:  T88312473
track2:  T90772488
track2:  T90272494
track2:  T90282503
track2:  T90292509
track2:  T91262524
track2:  T91292540
track2:  T92
track2:  T9212551
track2:  T93
track2:  T93472588
track2:  T93782591
track2:  T93482597
track2:  T93792609
track2:  T94
track2:  T94212629
track2:  T96
track2:  T96202680
track2:  T96852707
track2:  T96232732
track2:  T96672742
track2:  T9612748
track2:  T98232783
track2:  T98662801
track2:  T98672804
track2:  T9812813
track2:  T98812824
track2:  T98262831
track2:  T98862838
track2:  T98282844
track2:  T99
track2:  T101572871
track2:  T102
track2:  T103
track2:  T103622920
track2:  T103622928
track2:  T103262932
track2:  T103292963
track2:  T107
track2:  T109
track2:  T10933004
track2:  T110
track2:  T112
track2:  T113533029
track2:  T113893043
track2:  T113903046
track2:  T113893079
track2:  T115
track2:  T11993132
track2:  T120263154
track2:  T121763175
track2:  T122
track2:  T122863204
track2:  T122913215
tr

...

track2:  T311688385
track2:  T311888388
track2:  T311608394
track2:  T311318402
track2:  T3121078422
track2:  T313288443
track2:  T314748463
track2:  T31438472
track2:  T315238482
track2:  T315618490
track2:  T316
track2:  T316148501
track2:  T317228519
track2:  T319
track2:  T319808578
track2:  T320
track2:  T320538598
track2:  T320318607
track2:  T320198616
track2:  T32008621
track2:  T321728634
track2:  T32188640
track2:  T322
track2:  T322818678
track2:  T324
track2:  T324238722
T286
track1:  T286
track2:  T288
track2:  T290
track2:  T290677909
track2:  T291
track2:  T292
track2:  T292677943
track2:  T29217948
track2:  T292417958
track2:  T293287979
track2:  T293237987
track2:  T29318000
track2:  T294
track2:  T294678040
track2:  T295
track2:  T296
track2:  T297
track2:  T298928122
track2:  T3001008148
track2:  T301
track2:  T301818196
track2:  T302
track2:  T30218208
track2:  T302138215
track2:  T304268236
track2:  T305
track2:  T3051138254
track2:  T305238258
track2:  T305238264


track2:  T307
track2:  T30738352
track2:  T311
track2:  T311688385
track2:  T311888388
track2:  T311608394
track2:  T311318402
track2:  T3121078422
track2:  T313288443
track2:  T314748463
track2:  T31438472
track2:  T315238482
track2:  T315618490
track2:  T316
track2:  T316148501
track2:  T317228519
track2:  T319
track2:  T319808578
track2:  T320
track2:  T320538598
track2:  T320318607
track2:  T320198616
track2:  T32008621
track2:  T321728634
track2:  T32188640
track2:  T322
track2:  T322818678
track2:  T324
track2:  T324238722
T292417958
track1:  T292417958
track2:  T293287979
track2:  T293237987
track2:  T29318000
track2:  T294
track2:  T294678040
track2:  T295
track2:  T296
track2:  T297
track2:  T298928122
track2:  T3001008148
track2:  T301
track2:  T301818196
track2:  T302
track2:  T30218208
track2:  T302138215
track2:  T304268236
track2:  T305
track2:  T3051138254
track2:  T305238258
track2:  T305238264
track2:  T306
track2:  T306488278
track2:  T307
track2:  T30738352
track2:  

track2:  T317228519
track2:  T319
track2:  T319808578
track2:  T320
track2:  T320538598
track2:  T320318607
track2:  T320198616
track2:  T32008621
track2:  T321728634
track2:  T32188640
track2:  T322
track2:  T322818678
track2:  T324
track2:  T324238722
T298928122
track1:  T298928122
track2:  T3001008148
track2:  T301
track2:  T301818196
track2:  T302
track2:  T30218208
track2:  T302138215
track2:  T304268236
track2:  T305
track2:  T3051138254
track2:  T305238258
track2:  T305238264
track2:  T306
track2:  T306488278
track2:  T307
track2:  T30738352
track2:  T311
track2:  T311688385
track2:  T311888388
track2:  T311608394
track2:  T311318402
track2:  T3121078422
track2:  T313288443
track2:  T314748463
track2:  T31438472
track2:  T315238482
track2:  T315618490
track2:  T316
track2:  T316148501
track2:  T317228519
track2:  T319
track2:  T319808578
track2:  T320
track2:  T320538598
track2:  T320318607
track2:  T320198616
track2:  T32008621
track2:  T321728634
track2:  T32188640
track2:  T3

track2:  T3121078422
track2:  T313288443
track2:  T314748463
track2:  T31438472
track2:  T315238482
track2:  T315618490
track2:  T316
track2:  T316148501
track2:  T317228519
track2:  T319
track2:  T319808578
track2:  T320
track2:  T320538598
track2:  T320318607
track2:  T320198616
track2:  T32008621
track2:  T321728634
track2:  T32188640
track2:  T322
track2:  T322818678
track2:  T324
track2:  T324238722
T306
track1:  T306
track2:  T306488278
track2:  T307
track2:  T30738352
track2:  T311
track2:  T311688385
track2:  T311888388
track2:  T311608394
track2:  T311318402
track2:  T3121078422
track2:  T313288443
track2:  T314748463
track2:  T31438472
track2:  T315238482
track2:  T315618490
track2:  T316
track2:  T316148501
track2:  T317228519
track2:  T319
track2:  T319808578
track2:  T320
track2:  T320538598
track2:  T320318607
track2:  T320198616
track2:  T32008621
track2:  T321728634
track2:  T32188640
track2:  T322
track2:  T322818678
track2:  T324
track2:  T324238722
T306488278
track1:

track2:  T32188640
track2:  T322
track2:  T322818678
track2:  T324
track2:  T324238722
T319808578
track1:  T319808578
track2:  T320
track2:  T320538598
track2:  T320318607
track2:  T320198616
track2:  T32008621
track2:  T321728634
track2:  T32188640
track2:  T322
track2:  T322818678
track2:  T324
track2:  T324238722
T320
track1:  T320
track2:  T320538598
track2:  T320318607
track2:  T320198616
track2:  T32008621
track2:  T321728634
track2:  T32188640
track2:  T322
track2:  T322818678
track2:  T324
track2:  T324238722
T320538598
track1:  T320538598
track2:  T320318607
track2:  T320198616
track2:  T32008621
track2:  T321728634
track2:  T32188640
track2:  T322
track2:  T322818678
track2:  T324
track2:  T324238722
T320318607
track1:  T320318607
track2:  T320198616
track2:  T32008621
track2:  T321728634
track2:  T32188640
track2:  T322
track2:  T322818678
track2:  T324
track2:  T324238722
T320198616
track1:  T320198616
track2:  T32008621
track2:  T321728634
track2:  T32188640
track2:  T322


In [317]:
pd.DataFrame.to_csv(res, "./Needleman_Wunsch_result_1.csv", index=True)

In [ ]:
def align_tracks(track1, track2, gap_penalty):
    """ Needleman-Wunsch algorithm adapted for gps tracks. """
    
    _log.info("Aligning tracks")

    def similarity(p1, p2):
        d = gpxpy.geo.distance(p1.latitude, p1.longitude, p1.elevation,
                               p2.latitude, p2.longitude, p2.elevation)
        return -d

    # construct f-matrix
    f = numpy.zeros((len(track1), len(track2)))
    for i in range(0, len(track1)):
        f[i][0] = gap_penalty * i
    for j in range(0, len(track2)):
        f[0][j] = gap_penalty * j
    for i in range(1, len(track1)):
        t1 = track1[i]
        for j in range(1, len(track2)):
            t2 = track2[j]
            match = f[i-1][j-1] + similarity(t1, t2)
            delete = f[i-1][j] + gap_penalty<
            insert = f[i][j-1] + gap_penalty
            f[i, j] = max(match, max(delete, insert))

    # backtrack to create alignment
    a1 = []
    a2 = []
    i = len(track1) - 1
    j = len(track2) - 1
    while i > 0 or j > 0:
        if i > 0 and j > 0 and \
           f[i, j] == f[i-1][j-1] + similarity(track1[i], track2[j]):
            a1.insert(0, track1[i])
            a2.insert(0, track2[j])
            i -= 1
            j -= 1
        elif i > 0 and f[i][j] == f[i-1][j] + gap_penalty:
            a1.insert(0, track1[i])
            a2.insert(0, None)
            i -= 1
        elif j > 0 and f[i][j] == f[i][j-1] + gap_penalty:
            a1.insert(0, None)
            a2.insert(0, track2[j])
            j -= 1
    return a1, a2

align_tracks()